# Optimisation en Python
**Marc BUFFAT , Université Claude Bernard Lyon 1**

- *Premature optimization is the root of all evil (or at least most of it) in programming.*
    - Donald Knuth (créateur de TeX)
- *It's easier to optimize correct code than to correct optimized code.*
- *Avant toute optimisation, il faut d'abord écrire un code correct, documenté et validé.*

In [ ]:
# option de mise en page
from IPython.display import HTML,display
#from JSAnimation import IPython_display
#css_file = 'style.css'
#HTML(open(css_file, "r").read())

In [ ]:
%matplotlib inline
# bibliotheques de base
import matplotlib
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import rcParams
rcParams['font.family'] = 'serif'
rcParams['font.size'] = 14

## Calcul de la matrice de Vandermonde V (N,M)

Soit un vecteur $X$ de dimension $N$:

$$ V_{ij} = x_i ^{j-1} \;\; \forall i=1,N \;\; \forall j=1,n$$
- écrire un algorithme avec des boucles
- vectoriser la boucle interne et comparer

In [ ]:
# version avec des boucles
def Vandermonde_v1(X) :
    """Calcul de la matrice de VanderMonde V a partir de X"""
    N= X.size
    V= np.ones((N,N))
    for i in range(N) :
        for j in range(N) :
            V[i,j] = X[i]**j
    return V

In [ ]:
# donnees
N=100
X=np.linspace(0,1.,N)

In [ ]:
A1=Vandermonde_v1(X)
print(A1[:,0],A1[:,1])

In [ ]:
%%timeit -n 4
A=Vandermonde_v1(X)

### optimisation python 
  - vectorisation boucle interne
  - élimine la fonction **

In [ ]:
# version optimisee
def Vandermonde_v2(X) :
    N=X.size
    V=np.ones((N,N))
    for j in range(1,N):
        V[:,j]=V[:,j-1]*X[:]
    return V

In [ ]:
A2=Vandermonde_v2(X)
print(A2[:,0],A2[:,1])

In [ ]:
%%timeit -n 4
A=Vandermonde_v2(X)

## Cython

 - interface notebook ipython (+simple)
 - ou compilation explicite 

In [ ]:
%load_ext Cython

In [ ]:
%%cython
# reecriture en Cython
# ====================
#cython: boundscheck=False
#cython: wraparound=False
#
import numpy as np
cimport numpy  as np
cimport cython

cpdef np.ndarray[double,ndim=2] vandermonde(np.ndarray[double,ndim=1] X):
    cdef int N=X.size
    cdef np.ndarray[double,ndim=2] A = np.ones((N,N))
    cdef int i,j
    for j in xrange(1,N):
       for i in xrange(N):
         A[i,j] = A[i,j-1]*X[i]
    return A


In [ ]:
A3=vandermonde(X)
print(A3[:,0],A3[:,1])

### compilation explicite  cython 
 - creation code vandermonde.pyx en Cython
 - ecriture interface python (bibliotheque)
 - compilartion du code C genere

In [ ]:
%%bash
cat vandermonde.pyx

In [ ]:
%%bash
cat setup.py

In [ ]:
%%bash
python setup.py build_ext --inplace
./test_vandermonde.py 

### code C

In [ ]:
%%bash
cat vandermonde_C.C

In [ ]:
%%bash
g++ test_vandermondeC.C vandermonde_C.C -O3
./a.out 10 -d

## Démarche d'optimisation 

    « Premature optimization is the root of all evil (or at least most of it) in programming.»
        — Donald Knuth (créateur de TeX)
        
    « It's easier to optimize correct code than to correct optimized code.»
    
    "Un code correct et validé est indispensable. Un code optimisé non !"
        

## étape d'optimisation 

    1. écrire tout d'abord un code correcte et documenté
    2. valider le code
    3. faire du profiling (avec timeit) pour déterminer les fonctions les plus couteuses en temps CPU
    4. optimiser uniquement ces fonctions (en général 5 à 10% du code total)

## Optimisation sous Python
Dans l'ordre:
 1. utiliser les bibliothéques (numpy, scipy)
 2. vectoriser les boucles internes
 3. utiliser un compilateur python (Cython,..)
 4. réecrire le code en C/FORTRAN

## exemple: produit matrice vecteur

$ b = A*x $ avec
$$ b_i = \sum_j A_{ij} x_j $$

 - programme avec boucles
 - vectorisation
 - utilisation de numpy dot

In [ ]:
def produit(A,x):
    """ calcul b=Ax """
    n=x.size
    b=np.zeros(n)
    for i in range(n):
        for j in range(n):
            b[i] += A[i,j]*x[j]
    return b

In [ ]:
# version vectoriel 1
def produitv1(A,x):
    n=x.size
    b=np.zeros(n)
    for i in range(n):
        b[i] = np.sum(A[i,:]*x[:])
        #b[i] = sum(A[i,:]*x[:]) # attention sum
    return b

In [ ]:
# version vectoriel 2
def produitv2(A,x):
    B = A * x
    b = np.sum(B[:,:],axis=1)
    return b

In [ ]:
N=1000
A  = np.random.rand(N,N)
X  = np.random.rand(N)
B0 = np.dot(A,X)
B1 = produit(A,X)
B2 = produitv1(A,X) 
B3 = produitv2(A,X) 
print("erreur=",np.linalg.norm(B1-B0),\
                np.linalg.norm(B2-B0),\
                np.linalg.norm(B3-B0))

In [ ]:
%%timeit -n 2
B = produit(A,X)

In [ ]:
%%timeit -n 2
B = produitv1(A,X)

In [ ]:
%%timeit -n 2
B = produitv2(A,X)

In [ ]:
%%timeit -n 2
B = np.dot(A,X)

## FIN

In [ ]:
np.__version__